This code uses as an input the geojson file obtained as an output on the catastral_nodes notebook

In [1]:
import osmnx as ox
import pyproj
from pyproj import crs
print(pyproj.__version__)  # Should print the installed version


3.7.0


In [2]:
import geopandas as gpd

# Load the geojson file and print to check
nodes_gdf = gpd.read_file('./data/geojson/building_nodes_with_poi.geojson')

print(nodes_gdf.head())

  Referencia       lon        lat  nearest_node  time_to_nearest_poi  \
0    8594095 -1.948183  43.299723    2135506826             5.202316   
1    8594099 -1.948484  43.299120    2135506826             5.202316   
2    8594100 -1.948365  43.298748    2135506826             5.202316   
3    8796114 -1.928046  43.315046    6548202929             3.369070   
4    8796136 -1.928175  43.313904    6548202929             2.023299   

  block_color nearest_poi  nearest_poi_node                   geometry  
0      yellow     20-0004         457239233  POINT (-1.94818 43.29972)  
1      yellow     20-0004         457239233  POINT (-1.94848 43.29912)  
2      yellow     20-0004         457239233  POINT (-1.94837 43.29875)  
3       green     20-0178         533746770  POINT (-1.92805 43.31505)  
4       green     20-0019         476567754   POINT (-1.92818 43.3139)  


In [3]:
# Fill the time_to_poi column with None
nodes_gdf['time_to_nearest_poi'] = None
nodes_gdf['block_color'] = None
nodes_gdf['nearest_poi'] = None
nodes_gdf['nearest_poi_node'] = None
print(nodes_gdf.head())

  Referencia       lon        lat  nearest_node time_to_nearest_poi  \
0    8594095 -1.948183  43.299723    2135506826                None   
1    8594099 -1.948484  43.299120    2135506826                None   
2    8594100 -1.948365  43.298748    2135506826                None   
3    8796114 -1.928046  43.315046    6548202929                None   
4    8796136 -1.928175  43.313904    6548202929                None   

  block_color nearest_poi nearest_poi_node                   geometry  
0        None        None             None  POINT (-1.94818 43.29972)  
1        None        None             None  POINT (-1.94848 43.29912)  
2        None        None             None  POINT (-1.94837 43.29875)  
3        None        None             None  POINT (-1.92805 43.31505)  
4        None        None             None   POINT (-1.92818 43.3139)  


In [4]:
G_walk = ox.load_graphml(filepath="./data/networks/gipuzkoa_walk_with_geometry.graphml")

In [5]:
missing_geometry_edges = []

# Loop through all edges in the graph
for u, v, key, data in G_walk.edges(keys=True, data=True):
    if 'geometry' not in data:
        missing_geometry_edges.append((u, v, key))

# Print the edges with missing geometry
print("Edges missing geometry:", missing_geometry_edges)

Edges missing geometry: []


In [6]:
from shapely.geometry import LineString

# Rebuild geometry for missing edges
for u, v, key in missing_geometry_edges:
    # Retrieve the coordinates of the nodes
    u_coords = G_walk.nodes[u]['x'], G_walk.nodes[u]['y']
    v_coords = G_walk.nodes[v]['x'], G_walk.nodes[v]['y']
    
    # Create a LineString geometry between the two nodes
    new_geometry = LineString([u_coords, v_coords])
    
    # Assign the new geometry back to the edge
    G_walk[u][v][key]['geometry'] = new_geometry

In [7]:
poi = gpd.read_file('./data/poi/estetica.geojson')
print(poi.head())

  IDENTIFICADOR     DENOMINACIÓN DEL ESTABLECIMIENTO              DIRECCIÓN  \
0      L0328934  Kix - Kax Ileapaindegi eta Estetika  Calle Armendi Gain, 1   
1      L0432423                           Peluquería     Calle San Juan, 39   
2      L0310711                Peluquería y estética     Calle San Juan, 30   
3      L0190385               Larraitz Ileapaindegia   Barrio Larraitz, 2-A   
4      L0417371                Kixkur ile-apaindegia    Barrio Larraitz, 14   

    LOCALIDAD  CÓD. POSTAL MUNICIPIO TERRITORIO HISTÓRICO  CNAE  \
0         Aia        20809       Aia             Gipuzkoa  9602   
1      Alegia        20260    Alegia             Gipuzkoa  9602   
2      Alegia        20260    Alegia             Gipuzkoa  9602   
3  Errotaldea        20260    Alegia             Gipuzkoa  9602   
4  Errotaldea        20260    Alegia             Gipuzkoa  9602   

                             DESCRIPCIÓN CNAE ESTRATO EMPLEO  \
0  Peluquería y otros tratamientos de belleza            <

In [8]:
poi['lon'] = poi['geometry'].x
poi['lat'] = poi['geometry'].y

In [9]:
import networkx as nx

def get_nodes(row):
    orig_node = row['nearest_node']
    dest_node=row['nearest_poi_node']

In [10]:
import osmnx as ox
import pandas as pd

def nearest_node(row):
    if pd.isnull(row['lon']) or pd.isnull(row['lat']):
        return None  # Devuelve None si hay valores nulos
    return ox.distance.nearest_nodes(G_walk, X=row['lon'], Y=row['lat'])

poi['nearest_node'] = poi.apply(nearest_node, axis=1)
    
G_walk.graph['crs'] = "EPSG:4326"
poi['nearest_node'] = poi.apply(nearest_node, axis=1)

In [11]:
from shapely.geometry import Point

def nearest_poi(row, poi_df):
    # Asegúrate de usar la geometría para calcular la distancia
    distances = poi['geometry'].apply(lambda x: row.geometry.distance(x))
    nearest = poi.loc[distances.idxmin()]
    return nearest['DENOMINACIÓN DEL ESTABLECIMIENTO']  # cambiar según columna de POI que interese para identificar

# Aplica la función sobre cada fila del GeoDataFrame
nodes_gdf['nearest_poi'] = nodes_gdf.apply(nearest_poi, poi_df=poi, axis=1)

In [12]:
nodes_gdf['nearest_poi_node'] = None

# Get the nearest node of the nearest poi that is already in the poi dataframe
def nearest_poi_node(row):
    nearest_node = poi.loc[row['nearest_poi'] == poi['DENOMINACIÓN DEL ESTABLECIMIENTO']]['nearest_node']
    return nearest_node.values[0]

In [13]:
# Apply the function to each row in the GeoDataFrame
nodes_gdf['nearest_poi_node'] = nodes_gdf.apply(nearest_poi_node, axis=1)

In [14]:
import networkx as nx
import osmnx as ox
from shapely.geometry import LineString, MultiLineString
from shapely.ops import linemerge
import geopandas as gpd

def get_walk_time(row, G, walking_speed_mps=1.25):
    orig_node = row['nearest_node']
    dest_node = row['nearest_poi_node']
    
    try:
        # Find the shortest path based on distance or other weight suitable for walking
        route = nx.shortest_path(G, orig_node, dest_node, weight='length')  # Assuming 'length' is in meters        
        
        # Extract route geometries
        route_geometries = []
        for u, v in zip(route[:-1], route[1:]):
            edge_data = G.get_edge_data(u, v, 0)  # Handle multi-edges if needed
            if edge_data and 'geometry' in edge_data:
                route_geometries.append(edge_data['geometry'])
            else:
                print(f"Missing geometry for edge ({u}, {v})")
        
        # Merge all geometries into a single MultiLineString
        if route_geometries:
            route_geometry = linemerge(route_geometries)
        else:
            route_geometry = None
        
        # Calculate the route length
        if route_geometry:
            # Optionally, reproject to UTM for accurate length calculation
            route_gdf = gpd.GeoDataFrame(geometry=[route_geometry], crs="EPSG:4326")  # Use your CRS
            route_gdf = route_gdf.to_crs(epsg=32633)  # Replace with appropriate UTM zone
            route_geometry = route_gdf.geometry.iloc[0]
            route_length = route_geometry.length  # Length in meters
            print(f"Route length between node {orig_node} and node {dest_node} is {route_length} meters. Row index: {row.name}")
        else:
            route_length = 0
            print("No valid geometry found for the route.")
        
        # Calculate time based on walking speed (m/s)
        total_time_seconds = route_length / walking_speed_mps if route_length > 0 else None
        total_time_minutes = total_time_seconds / 60 if total_time_seconds else None
        
    except nx.NetworkXNoPath:
        print(f"No path found between node {orig_node} and node {dest_node}.")
        total_time_minutes = None  # No path
        route_length = 0  # No distance
    
    return total_time_minutes, route_length

In [15]:
nodes_gdf[['time_to_nearest_poi', 'distance_to_nearest_poi']] = nodes_gdf.apply(get_walk_time, G=G_walk, axis=1, result_type='expand')

Route length between node 2135506826 and node 457071686.0 is 1266.303632060177 meters. Row index: 0
Route length between node 2135506826 and node 457071686.0 is 1266.303632060177 meters. Row index: 1
Route length between node 2135506826 and node 457071686.0 is 1266.303632060177 meters. Row index: 2
Route length between node 6548202929 and node 6064007263.0 is 212.23130165259118 meters. Row index: 3
Route length between node 6548202929 and node 6064007263.0 is 212.23130165259118 meters. Row index: 4
Route length between node 8893267200 and node 259184972.0 is 12.471228945404988 meters. Row index: 5
Route length between node 12153786209 and node 482975138.0 is 28578.134030628622 meters. Row index: 6
Route length between node 455597094 and node 7595408770.0 is 271.6765302371532 meters. Row index: 7
Route length between node 455598339 and node 7595408770.0 is 222.09787552779252 meters. Row index: 8
Route length between node 293468945 and node 482975138.0 is 28421.824850662124 meters. Row i

In [16]:
print(nodes_gdf.head())

  Referencia       lon        lat  nearest_node  time_to_nearest_poi  \
0    8594095 -1.948183  43.299723    2135506826            16.884048   
1    8594099 -1.948484  43.299120    2135506826            16.884048   
2    8594100 -1.948365  43.298748    2135506826            16.884048   
3    8796114 -1.928046  43.315046    6548202929             2.829751   
4    8796136 -1.928175  43.313904    6548202929             2.829751   

  block_color           nearest_poi  nearest_poi_node  \
0        None                 Ascen      4.570717e+08   
1        None                 Ascen      4.570717e+08   
2        None                 Ascen      4.570717e+08   
3        None  Peluquería Estíbaliz      6.064007e+09   
4        None  Peluquería Estíbaliz      6.064007e+09   

                    geometry  distance_to_nearest_poi  
0  POINT (-1.94818 43.29972)              1266.303632  
1  POINT (-1.94848 43.29912)              1266.303632  
2  POINT (-1.94837 43.29875)              1266.303632  


In [17]:
# count rows with null values in the time_to_nearest_poi column
print(nodes_gdf['time_to_nearest_poi'].isnull().sum())

2649


In [18]:
# to these rows, assign time 0 if distance is 0
nodes_gdf.loc[nodes_gdf['time_to_nearest_poi'].isnull() & (nodes_gdf['distance_to_nearest_poi']==0), 'time_to_nearest_poi'] = 0

In [19]:
# count rows with null values in the time_to_nearest_poi column
print(nodes_gdf['time_to_nearest_poi'].isnull().sum())

0


In [20]:
# Assign colors to the blocks based on the time it takes to reach the nearest POI
nodes_gdf.loc[nodes_gdf['time_to_nearest_poi'] < 3, 'block_color'] = '#00572a'  # Dark Green
nodes_gdf.loc[(nodes_gdf['time_to_nearest_poi'] >= 3) & (nodes_gdf['time_to_nearest_poi'] < 6), 'block_color'] = '#7CB342'  # Green
nodes_gdf.loc[(nodes_gdf['time_to_nearest_poi'] >= 6) & (nodes_gdf['time_to_nearest_poi'] < 10), 'block_color'] = '#FFFF00'  # Yellow
nodes_gdf.loc[(nodes_gdf['time_to_nearest_poi'] >= 10) & (nodes_gdf['time_to_nearest_poi'] < 15), 'block_color'] = '#FFA500'  # Orange
nodes_gdf.loc[(nodes_gdf['time_to_nearest_poi'] >= 15) & (nodes_gdf['time_to_nearest_poi'] < 20), 'block_color'] = '#D50000'  # Red
nodes_gdf.loc[(nodes_gdf['time_to_nearest_poi'] >= 20) & (nodes_gdf['time_to_nearest_poi'] < 25), 'block_color'] = '#8f0340'  # Dark red
nodes_gdf.loc[nodes_gdf['time_to_nearest_poi'] >= 25, 'block_color'] = '#6a1717'  # Purple

In [21]:
# save gdf
nodes_gdf.to_file('./outputs/walk/estetica_times_walk.geojson', driver='GeoJSON')

In [22]:
# Assign colors to the blocks based on the time it takes to reach the nearest POI
nodes_gdf.loc[nodes_gdf['time_to_nearest_poi'] < 7, 'block_color'] = '#00572a'  # Dark Green
nodes_gdf.loc[(nodes_gdf['time_to_nearest_poi'] >= 7) & (nodes_gdf['time_to_nearest_poi'] < 15), 'block_color'] = '#7CB342'  # Green
nodes_gdf.loc[(nodes_gdf['time_to_nearest_poi'] >= 15) & (nodes_gdf['time_to_nearest_poi'] < 22), 'block_color'] = '#FFFF00'  # Yellow
nodes_gdf.loc[(nodes_gdf['time_to_nearest_poi'] >= 22) & (nodes_gdf['time_to_nearest_poi'] < 30), 'block_color'] = '#FFA500'  # Orange
nodes_gdf.loc[(nodes_gdf['time_to_nearest_poi'] >= 30) & (nodes_gdf['time_to_nearest_poi'] < 40), 'block_color'] = '#D50000'  # Red
nodes_gdf.loc[nodes_gdf['time_to_nearest_poi'] >= 40, 'block_color'] = '#8f0340'  # Burgundy
#nodes_gdf.loc[(nodes_gdf['time_to_nearest_poi'] >= 20) & (nodes_gdf['time_to_nearest_poi'] < 25), 'block_color'] = '#8f0340'  # Dark red
#nodes_gdf.loc[nodes_gdf['time_to_nearest_poi'] >= 25, 'block_color'] = '#6a1717'  # Purple

In [23]:
# save gdf
nodes_gdf.to_file('./outputs/walk/newcolors/estetica_nodes_times_walk_newcolors.geojson', driver='GeoJSON')

In [24]:
# count rows with inf values
print(nodes_gdf[nodes_gdf['time_to_nearest_poi'] == float('inf')].shape[0])

# print the rows with inf values
print(nodes_gdf[nodes_gdf['time_to_nearest_poi'] == float('inf')])

0
Empty GeoDataFrame
Columns: [Referencia, lon, lat, nearest_node, time_to_nearest_poi, block_color, nearest_poi, nearest_poi_node, geometry, distance_to_nearest_poi]
Index: []


In [25]:
nodes_bike=nodes_gdf
print(nodes_bike.head())
# drop the columns that are not needed
nodes_bike = nodes_bike.drop(columns=['time_to_nearest_poi', 'block_color'])

  Referencia       lon        lat  nearest_node  time_to_nearest_poi  \
0    8594095 -1.948183  43.299723    2135506826            16.884048   
1    8594099 -1.948484  43.299120    2135506826            16.884048   
2    8594100 -1.948365  43.298748    2135506826            16.884048   
3    8796114 -1.928046  43.315046    6548202929             2.829751   
4    8796136 -1.928175  43.313904    6548202929             2.829751   

  block_color           nearest_poi  nearest_poi_node  \
0     #FFFF00                 Ascen      4.570717e+08   
1     #FFFF00                 Ascen      4.570717e+08   
2     #FFFF00                 Ascen      4.570717e+08   
3     #00572a  Peluquería Estíbaliz      6.064007e+09   
4     #00572a  Peluquería Estíbaliz      6.064007e+09   

                    geometry  distance_to_nearest_poi  
0  POINT (-1.94818 43.29972)              1266.303632  
1  POINT (-1.94848 43.29912)              1266.303632  
2  POINT (-1.94837 43.29875)              1266.303632  


In [26]:
# iterate over the rows and calculate the time to the nearest POI dividing the distance by the average biking speed
for index, row in nodes_bike.iterrows():
    distance = row['distance_to_nearest_poi']
    time = distance / 2.6  # Average biking speed in m/s (adjusted to match google maps values)
    time_s=time/60
    nodes_bike.at[index, 'time_to_nearest_poi'] = time_s

# Assign colors to the blocks based on the time it takes to reach the nearest POI
nodes_bike.loc[nodes_bike['time_to_nearest_poi'] < 3, 'block_color'] = '#00572a'  # Dark Green
nodes_bike.loc[(nodes_bike['time_to_nearest_poi'] >= 3) & (nodes_bike['time_to_nearest_poi'] < 6), 'block_color'] = '#7CB342'  # Green
nodes_bike.loc[(nodes_bike['time_to_nearest_poi'] >= 6) & (nodes_bike['time_to_nearest_poi'] < 10), 'block_color'] = '#FFFF00'  # Yellow
nodes_bike.loc[(nodes_bike['time_to_nearest_poi'] >= 10) & (nodes_bike['time_to_nearest_poi'] < 15), 'block_color'] = '#FFA500'  # Orange
nodes_bike.loc[(nodes_bike['time_to_nearest_poi'] >= 15) & (nodes_bike['time_to_nearest_poi'] < 20), 'block_color'] = '#D50000'  # Red
nodes_bike.loc[(nodes_bike['time_to_nearest_poi'] >= 20) & (nodes_bike['time_to_nearest_poi'] < 25), 'block_color'] = '#8f0340'  # Dark red
nodes_bike.loc[nodes_bike['time_to_nearest_poi'] >= 25, 'block_color'] = '#6a1717'  # Purple

In [27]:
print(nodes_bike.head())

  Referencia       lon        lat  nearest_node           nearest_poi  \
0    8594095 -1.948183  43.299723    2135506826                 Ascen   
1    8594099 -1.948484  43.299120    2135506826                 Ascen   
2    8594100 -1.948365  43.298748    2135506826                 Ascen   
3    8796114 -1.928046  43.315046    6548202929  Peluquería Estíbaliz   
4    8796136 -1.928175  43.313904    6548202929  Peluquería Estíbaliz   

   nearest_poi_node                   geometry  distance_to_nearest_poi  \
0      4.570717e+08  POINT (-1.94818 43.29972)              1266.303632   
1      4.570717e+08  POINT (-1.94848 43.29912)              1266.303632   
2      4.570717e+08  POINT (-1.94837 43.29875)              1266.303632   
3      6.064007e+09  POINT (-1.92805 43.31505)               212.231302   
4      6.064007e+09   POINT (-1.92818 43.3139)               212.231302   

   time_to_nearest_poi block_color  
0             8.117331     #FFFF00  
1             8.117331     #FFFF00  

In [28]:
nodes_bike.to_file('./outputs/bike/estetica_nodes_times_bike.geojson', driver='GeoJSON')

In [29]:
# Assign colors to the blocks based on the time it takes to reach the nearest POI
nodes_bike.loc[nodes_bike['time_to_nearest_poi'] < 7, 'block_color'] = '#00572a'  # Dark Green
nodes_bike.loc[(nodes_bike['time_to_nearest_poi'] >= 7) & (nodes_bike['time_to_nearest_poi'] < 15), 'block_color'] = '#7CB342'  # Green
nodes_bike.loc[(nodes_bike['time_to_nearest_poi'] >= 15) & (nodes_bike['time_to_nearest_poi'] < 22), 'block_color'] = '#FFFF00'  # Yellow
nodes_bike.loc[(nodes_bike['time_to_nearest_poi'] >= 22) & (nodes_bike['time_to_nearest_poi'] < 30), 'block_color'] = '#FFA500'  # Orange
nodes_bike.loc[(nodes_bike['time_to_nearest_poi'] >= 30) & (nodes_bike['time_to_nearest_poi'] < 40), 'block_color'] = '#D50000'  # Red
nodes_bike.loc[nodes_bike['time_to_nearest_poi'] >= 40, 'block_color'] = '#8f0340'  # Burgundy
#nodes_bike.loc[(nodes_bike['time_to_nearest_poi'] >= 20) & (nodes_bike['time_to_nearest_poi'] < 25), 'block_color'] = '#8f0340'  # Dark red
#nodes_bike.loc[nodes_bike['time_to_nearest_poi'] >= 25, 'block_color'] = '#6a1717'  # Purple

In [30]:
nodes_bike.to_file('./outputs/bike/newcolors/estetica_nodes_times_bike_newcolors.geojson', driver='GeoJSON')